# 0.1 WavesExecuter

---

## Multiple Experiments

Consider a scenario, you have multiple circuits that you want to run at once.

Call `.measure()` one by one will be inefficient,
no to mention that you also need to call `.anlyze()` for their post-processing.

Here we provide a more efficient way solve this problem,
where the true power of Qurrium as experiment manage toolkit.

Althoght `WavesExecuter` has provided you to run multiple circuits at once by `.measure`.
But you can not set shots for each circuit for they run by same experiment.


### a. Import the instances


In [1]:
from qurry import WavesExecuter

experiment_workflow = WavesExecuter()

### b. Preparing quantum circuit

Prepare and add circuits to the `.wave` for later usage.


In [2]:
from qiskit import QuantumCircuit
from qurry.recipe import TrivialParamagnet, GHZ


def make_neel_circuit(n):
    qc = QuantumCircuit(n)
    for i in range(0, n, 2):
        qc.x(i)
    return qc


circuits_dict = {}

for i in range(2, 13, 2):
    circuits_dict[f"trivial_paramagnet_{i}_ms"] = TrivialParamagnet(i)
    circuits_dict[f"ghz_{i}_ms"] = GHZ(i)
    circuits_dict[f"neel_{i}_ms"] = make_neel_circuit(i)

for name, circuit in circuits_dict.items():
    circuit.measure_all()
    experiment_workflow.add(circuit, name)

### c. Execute multiple experiments at once

Let's demonstrate the true power of Qurrium.


In [3]:
from qurry.qurrium.wavesqurry.arguments import WavesExecuterMeasureArgs

Preparing a configuration list for multiple experiments with following parameters:

```python
class WavesExecuterMeasureArgs(total=False):
    """Output arguments for :meth:`output`."""
    shots: int
    """Number of shots."""
    tags: Optional[tuple[str, ...]]
    """The tags to be used for the experiment."""

    waves: Optional[list[Union[QuantumCircuit, Hashable]]]
    """The list of circuits to be measured."""
```


In [4]:
config_list: list[WavesExecuterMeasureArgs] = [
    {
        "shots": 1024,
        "waves": [f"{wave_names}_{i}_ms" for _ in range(10) for i in range(2, 13, 2)],
        "tags": (wave_names, f"size_{i}"),
    }
    for wave_names in ["trivial_paramagnet", "ghz", "neel"]
]
print(len(config_list))

3


The `.multiOutput` will return an id of this `multimanager` instance,
which can be used to get the results and post-process them.

Each `multimanager` will export the experiments in a folder you can specify
by setting `save_location` parameter with default location for current directory
where Python executed.
It will create a folder with the name of the `multimanager` instance,
and inside it will create a folder for storing each experiment data.

It will do firstly in the building process, but you can skip it by setting `skip_build_write=True` to save time.
After all experiments are executed, it will export secondly,
which can also be skipped by setting `skip_output_write=True` for no files output.


In [5]:
multi_exps1 = experiment_workflow.multiOutput(
    config_list,
    summoner_name="qurrium.waves_executer",  # you can name it whatever you want
    multiprocess_build=True,
    # Using multiprocessing to build the experiments,
    # it will be faster but take all the CPU
    skip_build_write=True,
    # Skip the writing of the experiment as files during the build,
    save_location=".",
    # Save the experiment as files in the current directory
    multiprocess_write=True,
    # Writing the experiment as files using multiprocessing,
)
multi_exps1

| MultiManager building...
| Write "qurrium.waves_executer.001", at location "qurrium.waves_executer.001"


| 0/3   0%|          | - MultiManager building... - 00:00 < ?

| MultiOutput running...


| 0/3   0%|          | -  - 00:00 < ?

| Export multimanager...


| 0/9 - Exporting MultiManager content... - 00:00 < ?

| No quantity to export.
| Export multi.config.json for a2b990a1-5983-4f37-9fc9-50435fa1f470


| 0/2 - Exporting experiments... - 00:00 < ?

| Exporting qurrium.waves_executer.001/qurryinfo.json...
| Exporting qurrium.waves_executer.001/qurryinfo.json done.


'a2b990a1-5983-4f37-9fc9-50435fa1f470'

In [6]:
experiment_workflow.multimanagers[multi_exps1]

<MultiManager(id="a2b990a1-5983-4f37-9fc9-50435fa1f470",
  name="qurrium.waves_executer.001",
  tags=(),
  jobstype="local",
  pending_strategy="tags",
  last_events={
    'output.001': '2025-06-25 13:41:02',},
  exps_num=3)>

### d. Take all `counts`


In [7]:
for exp_id, exp_instance in experiment_workflow.multimanagers[multi_exps1].exps.items():
    print(f"| {exp_id}:", exp_instance.afterwards.counts)
    print("-" * 20)

| b638afd0-0042-47ba-b311-360066d83be5: [{'00': 248, '10': 279, '11': 247, '01': 250}, {'1011': 62, '0000': 62, '0100': 80, '1100': 60, '1010': 60, '1110': 58, '1001': 58, '0101': 68, '0111': 57, '0011': 68, '0010': 66, '1111': 61, '0001': 69, '1000': 70, '0110': 68, '1101': 57}, {'001100': 19, '111010': 16, '110000': 17, '001111': 14, '101010': 19, '101100': 11, '100100': 16, '001110': 18, '111111': 19, '111100': 17, '011111': 15, '011011': 27, '100111': 10, '000100': 22, '110110': 18, '100011': 7, '101011': 11, '010000': 21, '001000': 16, '111101': 15, '000101': 15, '110011': 13, '101001': 20, '101111': 13, '111001': 9, '001010': 17, '101110': 26, '010101': 8, '100001': 15, '010011': 14, '101101': 22, '001101': 10, '100010': 15, '111000': 22, '000010': 14, '110101': 16, '010100': 18, '010111': 17, '110001': 11, '011010': 11, '011101': 15, '000001': 17, '110100': 15, '010110': 16, '110111': 25, '011100': 20, '110010': 15, '001001': 17, '101000': 24, '011001': 14, '011110': 13, '000000

### e. Read exported multimanager data


In [8]:
multi_exps1_reades = experiment_workflow.multiRead(
    save_location=".",
    summoner_name="qurrium.waves_executer.001",
)

| Retrieve qurrium.waves_executer.001...
| at: qurrium.waves_executer.001


| 0/3   0%|          | - Loading 3 experiments ... - 00:00 < ?

## Post-Process Availablities and Version Info


In [9]:
from qurry.process import AVAIBILITY_STATESHEET

AVAIBILITY_STATESHEET

 | Qurrium version: 0.13.0
---------------------------------------------------------------------------
 ### Qurrium Post-Processing
   - Backend Availability ................... Python Cython Rust   JAX   
 - randomized_measure
   - entangled_entropy.entropy_core_2 ....... Yes    Depr.  Yes    No    
   - entangle_entropy.purity_cell_2 ......... Yes    Depr.  Yes    No    
   - entangled_entropy_v1.entropy_core ...... Yes    Depr.  Yes    No    
   - entangle_entropy_v1.purity_cell ........ Yes    Depr.  Yes    No    
   - wavefunction_overlap.echo_core_2 ....... Yes    Depr.  Yes    No    
   - wavefunction_overlap.echo_cell_2 ....... Yes    Depr.  Yes    No    
   - wavefunction_overlap_v1.echo_core ...... Yes    Depr.  Yes    No    
   - wavefunction_overlap_v1.echo_cell ...... Yes    Depr.  Yes    No    
 - hadamard_test
   - purity_echo_core ....................... Yes    No     Yes    No    
 - magnet_square
   - magnsq_core ............................ Yes    No     Yes    No   